In [85]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import os
import csv

In [86]:
def read_csv(filename):
    skip_rows = list(range(1, 17))
    data = pd.read_csv(filename, sep=';', skiprows=skip_rows)
    return data

In [87]:

file_name = 'Riyahd_raw.csv'
df = read_csv(file_name)
df.columns

/tmp/ipykernel_3075037/3659192646.py:3: DtypeWarning: Columns (32,33,35) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv(filename, sep=';', skiprows=skip_rows)


Index(['Time', 'Irradiance onto horizontal plane ',
       'Diffuse Irradiation onto Horizontal Plane ', 'Outside Temperature ',
       'Module Area 1: Height of Sun ',
       'Module Area 1: Irradiance onto tilted surface ',
       'Module Area 1: Module Temperature ', 'Grid Export ',
       'Energy from Grid ', 'Global radiation - horizontal ',
       'Deviation from standard spectrum ', 'Ground Reflection (Albedo) ',
       'Orientation and inclination of the module surface ', 'Shading ',
       'Reflection on the Module Surface ',
       'Irradiance on the rear side of the module ',
       'Global Radiation at the Module ',
       'Module Area 1: Reflection on the Module Surface ',
       'Module Area 1: Global Radiation at the Module ',
       'Global PV Radiation ', 'Bifaciality ', 'Soiling ',
       'STC Conversion (Rated Efficiency of Module) ', 'Rated PV Energy ',
       'Low-light performance ', 'Module-specific Partial Shading ',
       'Deviation from the nominal module tem

In [88]:
remain_column = ['Time','PV energy (AC) minus standby use ']
energy_row_name = remain_column[1]

df = df[remain_column]
df[energy_row_name] = df[energy_row_name].str.replace(',','.').astype(float)


In [89]:
sum_energy = df[energy_row_name].sum()
sum_energy

770594.226863267

In [90]:
sum_energy / 390

1975.882632982736

In [91]:
group_size = 15
df['group_id'] = df.index // group_size

sums = df.groupby('group_id')[energy_row_name].sum()
sums_df = sums.reset_index(drop=True).to_frame(name = 'Energy')

In [92]:
sums_df.head

<bound method NDFrame.head of        Energy
0         0.0
1         0.0
2         0.0
3         0.0
4         0.0
...       ...
35035     0.0
35036     0.0
35037     0.0
35038     0.0
35039     0.0

[35040 rows x 1 columns]>

In [93]:

start_date = '2023-01-01'
end_date = '2023-12-31'

# 生成每天的15分钟间隔时间
all_dates = pd.date_range(start=start_date, end=end_date, freq='D')
all_times = pd.timedelta_range(start='0 min', end='1435 min', freq='15 min')

# 生成完整的时间标签
date_times = [pd.Timestamp(date) + time for date in all_dates for time in all_times]

# 创建DataFrame
time_frame = pd.DataFrame({
    'Time': date_times
})

# 查看生成的DataFrame
print(time_frame.head())
print(time_frame.tail())


                 Time
0 2023-01-01 00:00:00
1 2023-01-01 00:15:00
2 2023-01-01 00:30:00
3 2023-01-01 00:45:00
4 2023-01-01 01:00:00
                     Time
35035 2023-12-31 22:45:00
35036 2023-12-31 23:00:00
35037 2023-12-31 23:15:00
35038 2023-12-31 23:30:00
35039 2023-12-31 23:45:00


In [94]:
print(sums_df.shape)
print(time_frame.shape)

(35040, 1)
(35040, 1)


In [95]:
# sums_df['Time'] = time_frame['Time']
sums_df = pd.concat([time_frame, sums_df], axis=1)

In [96]:
sums_df.set_index('Time', inplace=True)
print(sums_df.head())

                     Energy
Time                       
2023-01-01 00:00:00     0.0
2023-01-01 00:15:00     0.0
2023-01-01 00:30:00     0.0
2023-01-01 00:45:00     0.0
2023-01-01 01:00:00     0.0


In [97]:
max_value = sums_df['Energy'].max()
sums_df['Energy'] = sums_df['Energy'] / max_value


In [98]:
def save_csv(df, filename, columns):
    tmp_df = df.copy()
    tmp_df[columns[1]] = tmp_df[columns[1]].round(4)
    with open(filename, 'w', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(columns)
        for index, row in tmp_df.iterrows():
            time_formatted = index.strftime('%H:%M')
            writer.writerow([time_formatted, row[columns[1]]])
            
        print(f'The file is written to {filename}')
        



In [99]:
save_csv(sums_df, 'Riyahd.csv', ['Time', 'Energy'])

The file is written to Riyahd.csv
